# Deep Learning for NLP - Project

RULES:

* Do not create any additional cell

* Fill in the blanks

* All cells should be runnable (modulo trivial compatibility bugs that we'd fix)

* 4 / 20 points will be allocated to the clarity of your code

* Efficient code will have a bonus

DELIVERABLE:

* the pdf with your answers
* this notebook
* the predictions of the SST test set

DO NOT INCLUDE THE DATASETS IN THE DELIVERABLE..

In [1]:
# Python 3.6 or above is required
from collections import defaultdict
import gzip
import numpy as np
from pathlib import Path
from urllib.request import urlretrieve

In [2]:
PATH_TO_DATA = Path('data/')
# Download word vectors, might take a few minutes and about ~3GB of storage space
en_embeddings_path = PATH_TO_DATA / 'cc.en.300.vec.gz'
if not en_embeddings_path.exists():
    urlretrieve('https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.en.300.vec.gz', en_embeddings_path)
fr_embeddings_path = PATH_TO_DATA / 'cc.fr.300.vec.gz'
if not fr_embeddings_path.exists():
    urlretrieve('https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.fr.300.vec.gz', fr_embeddings_path)

# 1) Monolingual (English) word embeddings 

In [3]:
class Word2Vec():

    def __init__(self, filepath, vocab_size=50000):
        self.words, self.embeddings = self.load_wordvec(filepath, vocab_size)
        # Mappings for O(1) retrieval:
        self.word2id = {word: idx for idx, word in enumerate(self.words)}
        self.id2word = {idx: word for idx, word in enumerate(self.words)}
    
    def load_wordvec(self, filepath, vocab_size):
        assert str(filepath).endswith('.gz')
        words = []
        embeddings = []
        with gzip.open(filepath, 'rt', encoding="utf8") as f:  # Read compressed file directly
            next(f)  # Skip header
            for i, line in enumerate(f):
                word, vec = line.split(' ', 1)
                words.append(word)
                embeddings.append(np.fromstring(vec, sep=' '))
                if i == (vocab_size - 1):
                    break
        print('Loaded %s pretrained word vectors' % (len(words)))
        return words, np.vstack(embeddings)
    
    def encode(self, word):
        # Returns the 1D embedding of a given word
#         raise NotImplementedError('Fill in the blank')
        return self.embeddings[self.word2id[word]]
    
    def score(self, word1, word2):
        # Return the cosine similarity: use np.dot & np.linalg.norm
#         raise NotImplementedError('Fill in the blank')
        enc_word1 = self.encode(word1)
        enc_word2 = self.encode(word2)
        return np.dot(enc_word1, enc_word2) / (np.linalg.norm(enc_word1) * np.linalg.norm(enc_word2))
    
    def most_similar(self, word, k=5):
        # Returns the k most similar words: self.score & np.argsort 
#         raise NotImplementedError('Fill in the blank')
        scores = []
        for word_key in self.word2id.keys():
            scores.append(self.score(word, word_key))
        indices = np.argsort(scores)[-k-1:-1] # In order to remove self similarity
        return [self.id2word[ind] for ind in reversed(indices)]

In [280]:
word2vec = Word2Vec(en_embeddings_path, vocab_size=50000)

# You will be evaluated on the output of the following:
for word1, word2 in zip(('cat', 'cat', 'cat', 'Paris', 'Paris', 'Paris', 'Paris'), ('tree', 'dog', 'pet', 'France', 'Germany', 'baguette', 'donut')):
    print(word1, word2, word2vec.score(word1, word2))
for word in ['cat', 'dog', 'dogs', 'Paris', 'Germany']:
    print(word2vec.most_similar(word))

Loaded 50000 pretrained word vectors
cat tree 0.2644975466165475
cat dog 0.7078641298542562
cat pet 0.6753313359976381
Paris France 0.6892958925806542
Paris Germany 0.4051242286737548
Paris baguette 0.29399958277802224
Paris donut -0.006588507552348005
['cats', 'kitty', 'kitten', 'feline', 'dog']
['dogs', 'puppy', 'pup', 'canine', 'pet']
['dog', 'cats', 'puppies', 'Dogs', 'pets']
['France', 'Parisian', 'Marseille', 'Brussels', 'Strasbourg']
['Austria', 'Europe', 'Berlin', 'Hamburg', 'Bavaria']


In [10]:
class BagOfWords():
    
    def __init__(self, word2vec):
        self.word2vec = word2vec
    
    def build_idf(self, sentences):
        # build the idf dictionary: associate each word to its idf value
        # -> idf = {word: idf_value, ...}
#         raise NotImplementedError('Fill in the blank')
        idf = dict()
        for sentence in sentences :
            sentence = sentence.split()
            for word in sentence :
                if word not in idf.keys():
                    idf[word]= 1
                else :
                    idf[word]+=1 
        for word in idf.keys():
            idf[word] = np.log10(len(sentences))/idf[word]
        return idf
    
    def encode(self, sentence, idf=None):
        # Takes a sentence as input, returns the sentence embedding
        if idf is None:
            # mean of word vectors
#             raise NotImplementedError('Fill in the blank')
            sentence = sentence.split()
            sentence = [w for w in sentence if w in self.word2vec.words]
            vectors = np.array([self.word2vec.encode(word) for word in sentence])
            mean_vector = np.mean(vectors, axis = 0)
            return mean_vector
        else:
            # idf-weighted mean of word vectors
#             raise NotImplementedError('Fill in the blank')
            sentence = sentence.split()
            sentence = [w for w in sentence if w in self.word2vec.words]
            vectors = np.array([self.word2vec.encode(word) for word in sentence])
            mean_vector = np.average(vectors, weights=[idf[word] for word in sentence], axis=0)
            return mean_vector
        
    def score(self, sentence1, sentence2, idf=None):
        # cosine similarity: use np.dot & np.linalg.norm 
#         raise NotImplementedError('Fill in the blank')
        enc_sentence1 = self.encode(sentence=sentence1, idf=idf)
        enc_sentence2 = self.encode(sentence=sentence2, idf=idf)
        return np.dot(enc_sentence1, enc_sentence2) / (np.linalg.norm(enc_sentence1) * np.linalg.norm(enc_sentence2))
    
    def most_similar(self, sentence, sentences, idf=None, k=5):
        # Return most similar sentences
#         raise NotImplementedError('Fill in the blank')
        scores = []
        for s in sentences :
            scores.append(self.score(sentence, s, idf))
        indices = np.argsort(scores)[-k-1:]
        return [sentences[ind] for ind in reversed(indices)]

In [292]:
word2vec = Word2Vec(en_embeddings_path, vocab_size=100000)
sentence2vec = BagOfWords(word2vec)

# Load sentences in "PATH_TO_DATA/sentences.txt"
filepath = PATH_TO_DATA / 'sentences.txt'
with open(filepath, 'r', encoding = "utf-8") as f:
    sentences = [line.strip('\n') for line in f]

# You will be evaluated on the output of the following:
print('\n\t--------------------------')
print('\n\tAverage of word embeddings')
print('\n\t--------------------------')
sentence1 = sentences[7]
sentence2 = sentences[13]
print(sentence1)
print(sentence2)
print(sentence2vec.score(sentence1, sentence2))
print('\n\t---------------------------------------')
sentence = sentences[10]
similar_sentences = sentence2vec.most_similar(sentence, sentences)  # BagOfWords-mean
print(sentence)
for i, sentence in enumerate(similar_sentences):
    print(str(i+1) + ')', sentence)

# Build idf scores for each word
idf, _ = sentence2vec.build_idf(sentences)

print('\n\t---------------------------------------')
print('\n\tidf weighted average of word embeddings')
print('\n\t---------------------------------------')
print(sentence1)
print(sentence2)
print(sentence2vec.score(sentence1, sentence2, idf))
print('\n\t---------------------------------------')
similar_sentences = sentence2vec.most_similar(sentence, sentences, idf)  # BagOfWords-idf
print(sentence)
for i, sentence in enumerate(similar_sentences):
    print(str(i+1) + ')', sentence)

Loaded 100000 pretrained word vectors

	--------------------------

	Average of word embeddings

	--------------------------
1 man singing and 1 man playing a saxophone in a concert . 
10 people venture out to go crosscountry skiing . 
0.7065220648251476

	---------------------------------------
1 smiling african american boy . 
1) 1 smiling african american boy . 
2) 2 woman dancing while pointing . 
3) 5 women and 1 man are smiling for the camera . 
4) a small boy following 4 geese . 
5) 2 female babies eating chips . 
6) a young boy and 2 girls open christmas presents . 

	---------------------------------------

	idf weighted average of word embeddings

	---------------------------------------
1 man singing and 1 man playing a saxophone in a concert . 
10 people venture out to go crosscountry skiing . 
0.45131736734105854

	---------------------------------------
a young boy and 2 girls open christmas presents . 
1) a young boy and 2 girls open christmas presents . 
2) two solders 

# 2) Multilingual (English-French) word embeddings

Let's consider a bilingual dictionary of size V_a (e.g French-English).

Let's define **X** and **Y** the **French** and **English** matrices.

They contain the embeddings associated to the words in the bilingual dictionary.

We want to find a **mapping W** that will project the source word space (e.g French) to the target word space (e.g English).

Procrustes : **W\* = argmin || W.X - Y ||  s.t  W^T.W = Id**
has a closed form solution:
**W = U.V^T  where  U.Sig.V^T = SVD(Y.X^T)**

In what follows, you are asked to: 

In [5]:
class MultilingualWordAligner:
    
    def __init__(self, fr_word2vec, en_word2vec):
        self.fr_word2vec = fr_word2vec
        self.en_word2vec = en_word2vec
        self.aligned_fr_embeddings = self.get_aligned_fr_embeddings()
        
    def get_aligned_fr_embeddings(self):
        # 1 - Get words that appear in both vocabs (= identical character strings)
        #     Use it to create the matrix X (emb_dim, vocab_size) and Y (emb_dim, vocab_size) (of embeddings for these words)
#         raise NotImplementedError('Fill in the blank')
        common_words = list(set(self.fr_word2vec.words) & set(self.en_word2vec.words))
        print("There are {} common words that are used as anchors in the two language spaces".format(len(common_words)))
        X = np.array([self.fr_word2vec.embeddings[self.fr_word2vec.word2id[word]] for word in common_words]).T
        Y = np.array([self.en_word2vec.embeddings[self.en_word2vec.word2id[word]] for word in common_words]).T
        assert X.shape[0] == 300 and Y.shape[0] == 300
        
        # 2 - Solve the Procrustes using the numpy package and: np.linalg.svd() and get the optimal W
        #     Now self.fr_word2vec.embeddings * W.transpose() is in the same space as en_word2vec.embeddings
#         raise NotImplementedError('Fill in the blank')
        U, Sigma, Vt = np.linalg.svd(Y.dot(X.T))
        W = np.dot(U, Vt)
        assert W.shape == (300, 300)
        return np.matmul(fr_word2vec.embeddings, W.transpose())
        
    def get_closest_english_words(self, fr_word, k=3):
        # 3 - Return the top k English nearest neighbors to the input French word
#         raise NotImplementedError('Fill in the blank')
        fr_in_en_space = self.aligned_fr_embeddings[self.fr_word2vec.word2id[fr_word]]
        norm_fr_word = np.linalg.norm(fr_in_en_space)
        scores = []
        for eng_word_emb in self.en_word2vec.embeddings :
            scores.append(np.dot(eng_word_emb, fr_in_en_space) / ( norm_fr_word * np.linalg.norm(eng_word_emb)))
        indices = np.argsort(scores)[-k:]
        return [self.en_word2vec.words[ind] for ind in reversed(indices)]

In [36]:
# fr_word2vec = Word2Vec(fr_embeddings_path, vocab_size=50000)
# en_word2vec = Word2Vec(en_embeddings_path, vocab_size=50000)
multilingual_word_aligner = MultilingualWordAligner(fr_word2vec, en_word2vec)

# You will be evaluated on the output of the following:
fr_words = ['chat', 'chien', 'voiture', 'zut']
k = 3
for fr_word in fr_words:
    print('-' * 10)
    print(f'fr: "{fr_word}"')
    en_words = multilingual_word_aligner.get_closest_english_words(fr_word, k=3)
    for en_word in en_words:
        print(f'en: "{en_word}"')

There are 14361 common words that are used as anchors in the two language spaces
----------
fr: "chat"
en: "cat"
en: "kitten"
en: "kitty"
----------
fr: "chien"
en: "dog"
en: "cat"
en: "pet"
----------
fr: "voiture"
en: "car"
en: "vehicle"
en: "automobile"
----------
fr: "zut"
en: "oops"
en: "Ah"
en: "ah"


If you want to dive deeper on this subject: https://github.com/facebookresearch/MUSE

# 3) Sentence classification with BoV and scikit-learn

In [3]:
# 1 - Load train/dev/test of Stanford Sentiment TreeBank (SST)
#     (https://nlp.stanford.edu/~socherr/EMNLP2013_RNTN.pdf)
train_filepath = PATH_TO_DATA / 'SST/stsa.fine.train'
dev_filepath = PATH_TO_DATA / 'SST/stsa.fine.dev'
test_filepath = PATH_TO_DATA / 'SST/stsa.fine.test.X'

# TYPE CODE HERE
with open(train_filepath,'r', encoding = "utf-8") as f:
    train = f.read().splitlines()
y_train = [int(s[0]) for s in train]
X_train = [s[2:] for s in train]

with open(dev_filepath,'r', encoding = "utf-8") as f:
    dev = f.read().splitlines()
y_dev = [int(s[0]) for s in dev]
X_dev = [s[2:] for s in dev]

In [11]:
# 2 - Encode sentences with the BoV model above

# TYPE CODE HERE
word2vec = Word2Vec(en_embeddings_path, vocab_size=100000)
sentence2vec = BagOfWords(word2vec)

X_train_embeddings_avg = np.array([sentence2vec.encode(sentence) for sentence in X_train])
X_dev_embeddings_avg = np.array([sentence2vec.encode(sentence) for sentence in X_dev])

### Handling the problem of new words in the dev set and not in the train set
### We treat them as a word in a new document
idf = sentence2vec.build_idf(X_train)
words_dev = []
for sentence in X_dev :
    for w in sentence.split():
        words_dev.append(w)
        
words_dev = set(words_dev)
for word in words_dev:
    if word not in idf.keys():
        idf[word] = np.log10(len(X_train)+1)
        
X_train_embeddings_wgt_avg = np.array([sentence2vec.encode(sentence, idf) for sentence in X_train])
X_dev_embeddings_wgt_avg = np.array([sentence2vec.encode(sentence, idf) for sentence in X_dev])

Loaded 100000 pretrained word vectors


In [14]:
# 3 - Learn Logistic Regression on top of sentence embeddings using scikit-learn
#     (consider tuning the L2 regularization on the dev set)
#     In the paper, the accuracy for average of word vectors is 32.7%
#     (VecAvg, table 1, https://nlp.stanford.edu/~socherr/EMNLP2013_RNTN.pdf)

# TYPE CODE HERE
from sklearn.linear_model import LogisticRegressionCV
from sklearn.metrics import accuracy_score

lr_avg = LogisticRegressionCV(cv=3, multi_class='multinomial', solver='lbfgs', max_iter=1000)
lr_avg.fit(X_train_embeddings_avg, y_train)

print(f'Training accuracy: {accuracy_score(y_train, lr_avg.predict(X_train_embeddings_avg))}')
print(f'Dev accuracy: {accuracy_score(y_dev, lr_avg.predict(X_dev_embeddings_avg))}')

print("----"*20)

lr_wgt_avg = LogisticRegressionCV(cv=3, multi_class='multinomial', solver='lbfgs', max_iter=1000)
lr_wgt_avg.fit(X_train_embeddings_wgt_avg, y_train)

print(f'Training accuracy: {accuracy_score(y_train, lr_wgt_avg.predict(X_train_embeddings_wgt_avg))}')
print(f'Dev accuracy: {accuracy_score(y_dev, lr_wgt_avg.predict(X_dev_embeddings_wgt_avg))}')



C:\Users\Houcine's laptop\AppData\Roaming\Python\Python37\site-packages\sklearn\linear_model\logistic.py:947: ConvergenceWarning: lbfgs failed to converge. Increase the number of iterations.
  "of iterations.", ConvergenceWarning)
C:\Users\Houcine's laptop\AppData\Roaming\Python\Python37\site-packages\sklearn\linear_model\logistic.py:947: ConvergenceWarning: lbfgs failed to converge. Increase the number of iterations.
  "of iterations.", ConvergenceWarning)
C:\Users\Houcine's laptop\AppData\Roaming\Python\Python37\site-packages\sklearn\linear_model\logistic.py:947: ConvergenceWarning: lbfgs failed to converge. Increase the number of iterations.
  "of iterations.", ConvergenceWarning)


Training accuracy: 0.45646067415730335
Dev accuracy: 0.40962761126248864
--------------------------------------------------------------------------------
Training accuracy: 0.4135065543071161
Dev accuracy: 0.371480472297911
--------------------------------------------------------------------------------


In [4]:
# 4 - Produce 2210 predictions for the test set (in the same order). One line = one prediction (=0,1,2,3,4).
#     Attach the output file "logreg_bov_y_test_sst.txt" to your deliverable.
#     You will be evaluated on the results of the test set.

# TYPE CODE HERE
with open(test_filepath,'r', encoding = "utf-8") as f:
    test = f.read().splitlines()
X_test = [s for s in test]
X_test_embeddings_avg = np.array([sentence2vec.encode(sentence) for sentence in X_test])

def submit(out_path, prediction):
    #function that write the submission
    lines = '\n'.join([str(p) for p in prediction])
    with open(out_path,'w') as f:
        f.writelines(lines)
        
predictions = lr_avg.predict(X_test_embeddings_avg)
submit('./logreg_bov_y_test_sst.txt',predictions)

NameError: name 'sentence2vec' is not defined

In [225]:
# BONUS!
# 5 - Try to improve performance with another classifier
#     Attach the output file "XXX_bov_y_test_sst.txt" to your deliverable (where XXX = the name of the classifier)

# TYPE CODE HERE
# from nltk.corpus import stopwords
# stpwrds = stopwords.words('english')

def clean_sentences(sen):
    
    # First lower case it : we saw that many similar words are mapped to different embeddings (Cat, cat)
    sen = sen.lower() 
    
    # Secondly we are going to the sentences from special characters that have embeddings
    # but that are not useful (pontuation, asterisk..)
#     ascii_range_numbers = list(range(48, 58))
#     ascii_capital_case = list(range(65,91))
#     ascii_lower_case = list(range(97, 123))
#     ascii_accents = list(range(192, 254))
#     ascii_space_dot_qst = [32, 46, 63]
#     valid_characters = ascii_range_numbers + ascii_capital_case + ascii_lower_case + ascii_accents + ascii_space_dot_qst
#     for char in sen :
#         if ord(char) not in valid_characters:
#             sen = sen.replace(char,"") 
    
    # clear the sentence from stopwords (the, and, ...)
    sen = sen.split()
    L = " ".join([word for word in sen if word not in stpwrds])
    return L

X_train_clean = []
for sen in X_train :
    X_train_clean.append(clean_sentences(sen))

X_dev_clean = []
for sen in X_dev :
    X_dev_clean.append(clean_sentences(sen))

X_train_embeddings_avg = np.array([sentence2vec.encode(sentence) for sentence in X_train])
X_dev_embeddings_avg = np.array([sentence2vec.encode(sentence) for sentence in X_dev])

from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, VotingClassifier
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV

clf1 = LinearSVC(class_weight="balanced")
# clf2 = RandomForestClassifier(n_estimators=100)
clf3 = GradientBoostingClassifier(n_estimators=100)
clf4 = LogisticRegression(C=2.78, multi_class='multinomial', solver='lbfgs', max_iter=1000)

eclf = VotingClassifier(estimators=[('svm', clf1), 
#                                     ('rf', clf2), 
                                    ('xgb', clf3),
                                    ("lr", clf4)
                                   ],
                        voting='hard')

eclf.fit(X_train_embeddings_avg, y_train)

print(f'Training accuracy: {accuracy_score(y_train, eclf.predict(X_train_embeddings_avg))}')
print(f'Dev accuracy: {accuracy_score(y_dev, eclf.predict(X_dev_embeddings_avg))}')
predictions = eclf.predict(X_test_embeddings_avg)
submit('./voting_bov_y_test_sst.txt',predictions)

Training accuracy: 0.5443586142322098
Dev accuracy: 0.4114441416893733


# 4) Sentence classification with LSTMs in Keras

## 4.1 - Preprocessing

In [1]:
import tensorflow as tf
from keras.utils import to_categorical

Using TensorFlow backend.


In [2]:
# 1 - Using the same dataset, transform text to integers using tf.keras.preprocessing.text.one_hot function
#     https://keras.io/preprocessing/text/

# TYPE CODE HERE
# keras.preprocessing.text.one_hot(text, n, filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n', lower=True, split=' ')

# Load sentences in "PATH_TO_DATA/sentences.txt"
PATH_TO_DATA = Path('data/')
train_filepath = PATH_TO_DATA / 'SST/stsa.fine.train'
dev_filepath = PATH_TO_DATA / 'SST/stsa.fine.dev'
test_filepath = PATH_TO_DATA / 'SST/stsa.fine.test.X'

with open(train_filepath,'r', encoding = "utf-8") as f:
    train = f.read().splitlines()
y_train = [int(s[0]) for s in train]
X_train = [s[2:] for s in train]

with open(dev_filepath,'r', encoding = "utf-8") as f:
    dev = f.read().splitlines()
y_dev = [int(s[0]) for s in dev]
X_dev = [s[2:] for s in dev]

with open(test_filepath,'r', encoding = "utf-8") as f:
    test = f.read().splitlines()
X_test = [s for s in test]

L = []
for sent in X_train + X_dev + X_test :
    for w in sent.split():
        L.append(w)
voc_size = len(set(L))
X_train_oh = []
for sen in X_train :
    X_train_oh.append(keras.preprocessing.text.one_hot(sen,
                                     n=voc_size,
                                     filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
                                     lower=True,
                                     split=' '))
    
X_dev_oh = []
for sen in X_dev :
    X_dev_oh.append(keras.preprocessing.text.one_hot(sen,
                                     n=voc_size,
                                     filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
                                     lower=True,
                                     split=' '))
X_test_oh = []
for sen in X_test :
    X_test_oh.append(keras.preprocessing.text.one_hot(sen,
                                     n=voc_size,
                                     filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
                                     lower=True,
                                     split=' '))

y_train_ = to_categorical(y_train)
y_dev_ = to_categorical(y_dev)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



**Padding input data**

Models in Keras (and elsewhere) take batches of sentences of the same length as input. It is because Deep Learning framework have been designed to handle well Tensors, which are particularly suited for fast computation on the GPU.

Since sentences have different sizes, we "pad" them. That is, we add dummy "padding" tokens so that they all have the same length.

The input to a Keras model thus has this size : (batchsize, maxseqlen) where maxseqlen is the maximum length of a sentence in the batch.

In [3]:
# 2 - Pad your sequences using tf.keras.preprocessing.sequence.pad_sequences
#     https://keras.io/preprocessing/sequence/

# TYPE CODE HERE
max_len = max([len(sen) for sen in X_train_oh+X_dev_oh+X_test_oh])
X_train_oh_pad = tf.keras.preprocessing.sequence.pad_sequences(X_train_oh, maxlen = max_len)
X_dev_oh_pad = tf.keras.preprocessing.sequence.pad_sequences(X_dev_oh, maxlen = max_len)
X_test_oh_pad = tf.keras.preprocessing.sequence.pad_sequences(X_test_oh, maxlen = max_len)

## 4.2 - Design and train your model

In [4]:
# 3 - Design your encoder + classifier using tensorflow.keras.layers
#     In Keras, Torch and other deep learning framework, we create a "container" which is the Sequential() module.
#     Then we add components to this container : the lookup-table, the LSTM, the classifier etc.
#     All of these components are contained in the Sequential() and are trained together.
#     Note that the embedding layer is initialized randomly and does not take advantage of pre-trained word embeddings.


# ADAPT CODE BELOW


from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Activation

embed_dim  = 32  # word embedding dimension
nhid       = 64  # number of hidden units in the LSTM
vocab_size = 50000  # size of the vocabulary
n_classes  = 5

model = Sequential()
model.add(Embedding(vocab_size, embed_dim))
model.add(LSTM(nhid, dropout=0.2, recurrent_dropout=0.2))
model.add(Dense(n_classes, activation='sigmoid'))

In [5]:
# 4 - Define your loss/optimizer/metrics

# MODIFY CODE BELOW

loss_classif     =  'categorical_crossentropy' # find the right loss for multi-class classification
optimizer        =  'rmsprop' # find the right optimizer
metrics_classif  =  ['accuracy']

# Observe how easy (but blackboxed) this is in Keras
model.compile(loss=loss_classif,
              optimizer=optimizer,
              metrics=metrics_classif)
print(model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, None, 32)          1600000   
_________________________________________________________________
lstm (LSTM)                  (None, 64)                24832     
_________________________________________________________________
dense (Dense)                (None, 5)                 325       
Total params: 1,625,157
Trainable params: 1,625,157
Non-trainable params: 0
_________________________________________________________________
None


In [6]:
# 5 - Train your model and find the best hyperparameters for your dev set
#     you will be evaluated on the quality of your predictions on the test set
#     Keras expects y_train and y_dev to be one-hot encodings of the labels, i.e. with shape=(n_samples, 5)


# ADAPT CODE BELOW
bs = 64
n_epochs = 6

history = model.fit(X_train_oh_pad, np.array(y_train_), batch_size=bs, nb_epoch=n_epochs, validation_data=(X_dev_oh_pad, np.array(y_dev_)))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Train on 8544 samples, validate on 1101 samples
Epoch 1/6
8544/8544 [==============================] - 13s 2ms/sample - loss: 1.5732 - accuracy: 0.2702 - val_loss: 1.5690 - val_accuracy: 0.3097
Epoch 2/6
8544/8544 [==============================] - 10s 1ms/sample - loss: 1.5434 - accuracy: 0.3119 - val_loss: 1.4979 - val_accuracy: 0.3370
Epoch 3/6
8544/8544 [==============================] - 9s 1ms/sample - loss: 1.4309 - accuracy: 0.3745 - val_loss: 1.4376 - val_accuracy: 0.3615
Epoch 4/6
8544/8544 [==============================] - 9s 1ms/sample - loss: 1.3068 - accuracy: 0.4163 - val_loss: 1.3857 - val_accuracy: 0.3787
Epoch 5/6
8544/8544 [==============================] - 9s 1ms/sample - loss: 1.2186 - accuracy: 0.4436 - val_loss: 1.4020 - val_accuracy: 0.3760
Epoch 6/6
8544/8544 [==============================] - 9s 1ms/sample - loss: 1.1496 - accuracy: 0.4662 - val_loss: 1.4308 - val_accuracy: 0.3887


In [7]:
plt.figure(figsize=(15,7))
plt.subplot(1,2,1)
plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('Provided model loss')
plt.ylabel('loss')
plt.xlabel('epoch')
plt.legend(['train', 'test']);

plt.subplot(1,2,2)
plt.plot(history.history['accuracy'])
plt.plot(history.history['val_accuracy'])
plt.title('Provided model accuracy')
plt.ylabel('accuracy')
plt.xlabel('epoch')
plt.legend(['train', 'test']);

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [8]:
# 6 - Generate your predictions on the test set using model.predict(x_test)
#     https://keras.io/models/model/
#     Log your predictions in a file (one line = one integer: 0,1,2,3,4)
#     Attach the output file "logreg_lstm_y_test_sst.txt" to your deliverable.

# TYPE CODE HERE
bs = 64
n_epochs = 3

history = model.fit(x=np.concatenate([X_train_oh_pad, X_dev_oh_pad]),
                    y=np.concatenate([y_train_,y_dev_]),
                    batch_size=bs,
                    nb_epoch=n_epochs)
predictions = np.argmax(model.predict(X_test_oh_pad), axis=1)
with open("logreg_LSTM_y_test_sst.txt", "w") as f:
    for label in predictions:
        f.write(label.astype('str')+'\n')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Train on 9645 samples
Epoch 1/3
9645/9645 [==============================] - 10s 1ms/sample - loss: 1.1292 - accuracy: 0.4719
Epoch 2/3
9645/9645 [==============================] - 10s 1ms/sample - loss: 1.0690 - accuracy: 0.5017
Epoch 3/3
9645/9645 [==============================] - 10s 1ms/sample - loss: 1.0182 - accuracy: 0.5316


<IPython.core.display.Javascript object>

## 4.3 - innovate !

In [23]:
# 7 - Open question: find a model that is better on your dev set
#     (e.g: use a 1D ConvNet, use a better classifier, pretrain your lookup tables ..)
#     you will get point if the results on the test set are better: be careful of not overfitting your dev set too much..
#     Attach the output file "XXX_XXX_y_test_sst.txt" to your deliverable.

# TYPE CODE HERE
# Python 3.6 or above is required
from collections import defaultdict
import gzip
import numpy as np
from pathlib import Path
from urllib.request import urlretrieve

import tensorflow as tf
from keras.preprocessing.text import Tokenizer
from keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Activation, Bidirectional

# Load sentences in "PATH_TO_DATA/sentences.txt"
PATH_TO_DATA = Path('data/')
train_filepath = PATH_TO_DATA / 'SST/stsa.fine.train'
dev_filepath = PATH_TO_DATA / 'SST/stsa.fine.dev'
test_filepath = PATH_TO_DATA / 'SST/stsa.fine.test.X'

def read_parse_X_y(file_path, flag=None ):
    with open(file_path,'r', encoding = "utf-8") as f:
        data = f.read().splitlines()
    if flag == "test":
        y = None
        X = [s for s in data]
    else :
        
        y = [int(s[0]) for s in data]
        X = [s[2:] for s in data]
    return X, y

def load_X_y(mode = "training"):
    if mode == "training" :
        X_train, y_train = read_parse_X_y(train_filepath)
        X_dev, y_dev = read_parse_X_y(dev_filepath)
        X_test, _ = read_parse_X_y(test_filepath, flag = "test")
        return X_train, X_dev, X_test, y_train, y_dev
    
    if mode == "final" :
        X_train, y_train = read_parse_X_y(train_filepath)
        X_dev, y_dev = read_parse_X_y(dev_filepath)
        X_test, y_test = read_parse_X_y(test_filepath, flag = "test")
        return np.concatenate((X_train, X_dev)), X_test, np.concatenate((y_train, y_dev)), y_test

X_train, X_dev, X_test, y_train, y_dev = load_X_y()



In [24]:
embed_dim  = 50  # word embedding dimension
nhid       = 64  # number of hidden units in
vocab_size = 50000  # size of the vocabulary
n_classes  = 5
dropout_rate = .3

## Preprocess the words in all datasets (Train, dev, test)
tokenizer = Tokenizer(nb_words=vocab_size)
texts = X_train + X_dev + X_test
tokenizer.fit_on_texts(texts)
sequences = tokenizer.texts_to_sequences(texts)
word_index = tokenizer.word_index

print('Found %s unique tokens.' % len(word_index))

MAX_SEQUENCE_LENGTH = max([len(sen) for sen in sequences])
data = tf.keras.preprocessing.sequence.pad_sequences(sequences, maxlen=MAX_SEQUENCE_LENGTH)

labels = to_categorical(np.asarray(y_train + y_dev))
print('Shape of data tensor:', data.shape)
print('Shape of label tensor:', labels.shape)

# split the data into a training set and a validation set

x_train = data[:len(X_train)]
x_dev = data[len(X_train):len(X_train)+len(X_dev)]
y_train__ = labels[:len(X_train)]
y_dev__ = labels[len(X_train):len(X_train)+len(X_dev)]

embeddings_index = {}
f = open(os.path.join('', 'glove.6B.50d.txt'),encoding = "utf-8")
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()



d:\anaconda\lib\site-packages\keras_preprocessing\text.py:178: UserWarning: The `nb_words` argument in `Tokenizer` has been renamed `num_words`.
  warnings.warn('The `nb_words` argument in `Tokenizer` '


Found 17839 unique tokens.
Shape of data tensor: (11855, 52)
Shape of label tensor: (9645, 5)


<IPython.core.display.Javascript object>

In [25]:
print('Found %s word vectors.' % len(embeddings_index))

embedding_matrix = np.zeros(( len(word_index)+1, embed_dim))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector
        
embedding_layer = Embedding(len(word_index) + 1,
                            embed_dim,
                            weights=[embedding_matrix],
                            input_length=MAX_SEQUENCE_LENGTH,
                            trainable=False,
                            name="emb_layer")


Found 400000 word vectors.


In [26]:
model1 = Sequential(name='Name')
model1.add(embedding_layer)
model1.add(Bidirectional(LSTM(nhid, 
                              dropout=dropout_rate, 
                              recurrent_dropout=dropout_rate, 
                              name="LSTM_1",
                              return_sequences=True),
#                          input_shape = (52,50),
                         name="Bidirectional_1"))
model1.add(Bidirectional(LSTM(nhid, 
                              dropout=dropout_rate, 
                              recurrent_dropout=dropout_rate, 
                              name="LSTM_2"),
                         name="Bidirectional_2"))
model1.add(Dense(n_classes, activation='softmax'))

In [27]:
model1.summary()

Model: "Name"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
emb_layer (Embedding)        (None, 52, 50)            892000    
_________________________________________________________________
Bidirectional_1 (Bidirection (None, 52, 128)           58880     
_________________________________________________________________
Bidirectional_2 (Bidirection (None, 128)               98816     
_________________________________________________________________
dense_1 (Dense)              (None, 5)                 645       
Total params: 1,050,341
Trainable params: 158,341
Non-trainable params: 892,000
_________________________________________________________________


In [28]:
loss_classif     =  'categorical_crossentropy' # find the right loss for multi-class classification
optimizer        =  'rmsprop' # find the right optimizer
metrics_classif  =  ['accuracy']

# Observe how easy (but blackboxed) this is in Keras
model1.compile(loss=loss_classif,
              optimizer=optimizer,
              metrics=metrics_classif)

bs = 32
n_epochs = 6

history = model1.fit(x_train, np.array(y_train__), batch_size=bs, nb_epoch=n_epochs, validation_data=(x_dev, np.array(y_dev__)))

Train on 8544 samples, validate on 1101 samples
Epoch 1/6
8544/8544 [==============================] - 51s 6ms/sample - loss: 1.5232 - accuracy: 0.3208 - val_loss: 1.4322 - val_accuracy: 0.3724
Epoch 2/6
8544/8544 [==============================] - 45s 5ms/sample - loss: 1.4746 - accuracy: 0.3455 - val_loss: 1.4184 - val_accuracy: 0.3824
Epoch 3/6
8544/8544 [==============================] - 46s 5ms/sample - loss: 1.4476 - accuracy: 0.3605 - val_loss: 1.3925 - val_accuracy: 0.3633
Epoch 4/6
8544/8544 [==============================] - 44s 5ms/sample - loss: 1.4265 - accuracy: 0.3687 - val_loss: 1.3698 - val_accuracy: 0.3860
Epoch 5/6
8544/8544 [==============================] - 44s 5ms/sample - loss: 1.4159 - accuracy: 0.3749 - val_loss: 1.3587 - val_accuracy: 0.3869
Epoch 6/6
8544/8544 [==============================] - 46s 5ms/sample - loss: 1.4025 - accuracy: 0.3835 - val_loss: 1.3485 - val_accuracy: 0.3951


***

In [29]:
embedding_layer = Embedding(len(word_index) + 1,
                            embed_dim,
                            weights=[embedding_matrix],
                            input_length=MAX_SEQUENCE_LENGTH,
                            trainable=True,
                            name="emb_layer")
model1 = Sequential(name='Name')
model1.add(embedding_layer)
model1.add(Bidirectional(LSTM(nhid, 
                              dropout=dropout_rate, 
                              recurrent_dropout=dropout_rate, 
                              name="LSTM_1",
                              return_sequences=True),
#                          input_shape = (52,50),
                         name="Bidirectional_1"))
model1.add(Bidirectional(LSTM(nhid, 
                              dropout=dropout_rate, 
                              recurrent_dropout=dropout_rate, 
                              name="LSTM_2"),
                         name="Bidirectional_2"))
model1.add(Dense(n_classes, activation='softmax'))
model1.summary()

Model: "Name"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
emb_layer (Embedding)        (None, 52, 50)            892000    
_________________________________________________________________
Bidirectional_1 (Bidirection (None, 52, 128)           58880     
_________________________________________________________________
Bidirectional_2 (Bidirection (None, 128)               98816     
_________________________________________________________________
dense_2 (Dense)              (None, 5)                 645       
Total params: 1,050,341
Trainable params: 1,050,341
Non-trainable params: 0
_________________________________________________________________


In [30]:
loss_classif     =  'categorical_crossentropy' # find the right loss for multi-class classification
optimizer        =  'rmsprop' # find the right optimizer
metrics_classif  =  ['accuracy']

# Observe how easy (but blackboxed) this is in Keras
model1.compile(loss=loss_classif,
              optimizer=optimizer,
              metrics=metrics_classif)

bs = 32
n_epochs = 10

history = model1.fit(x_train, np.array(y_train__), batch_size=bs, nb_epoch=n_epochs, validation_data=(x_dev, np.array(y_dev__)))

Train on 8544 samples, validate on 1101 samples
Epoch 1/10
8544/8544 [==============================] - 52s 6ms/sample - loss: 1.5120 - accuracy: 0.3209 - val_loss: 1.4469 - val_accuracy: 0.3388
Epoch 2/10
8544/8544 [==============================] - 46s 5ms/sample - loss: 1.4290 - accuracy: 0.3633 - val_loss: 1.3502 - val_accuracy: 0.3824
Epoch 3/10
8544/8544 [==============================] - 45s 5ms/sample - loss: 1.3777 - accuracy: 0.4022 - val_loss: 1.3186 - val_accuracy: 0.3960
Epoch 4/10
8544/8544 [==============================] - 45s 5ms/sample - loss: 1.3279 - accuracy: 0.4167 - val_loss: 1.3138 - val_accuracy: 0.4124
Epoch 5/10
8544/8544 [==============================] - 45s 5ms/sample - loss: 1.2836 - accuracy: 0.4396 - val_loss: 1.2878 - val_accuracy: 0.4187
Epoch 6/10
8544/8544 [==============================] - 45s 5ms/sample - loss: 1.2526 - accuracy: 0.4500 - val_loss: 1.2924 - val_accuracy: 0.4269
Epoch 7/10
8544/8544 [==============================] - 45s 5ms/sample

In [37]:
bs = 32
n_epochs = 8

history = model1.fit(x=np.concatenate([x_train, x_dev]),
                    y=np.concatenate([y_train__,y_dev__]),
                    batch_size=bs,
                    nb_epoch=n_epochs)

Train on 9645 samples
Epoch 1/8
9645/9645 [==============================] - 51s 5ms/sample - loss: 1.1230 - accuracy: 0.5146
Epoch 2/8
9645/9645 [==============================] - 50s 5ms/sample - loss: 1.1023 - accuracy: 0.5337
Epoch 3/8
9645/9645 [==============================] - 52s 5ms/sample - loss: 1.0656 - accuracy: 0.5438
Epoch 4/8
9645/9645 [==============================] - 50s 5ms/sample - loss: 1.0443 - accuracy: 0.5554
Epoch 5/8
9645/9645 [==============================] - 52s 5ms/sample - loss: 1.0167 - accuracy: 0.5671
Epoch 6/8
9645/9645 [==============================] - 54s 6ms/sample - loss: 0.9982 - accuracy: 0.5812
Epoch 7/8
9645/9645 [==============================] - 50s 5ms/sample - loss: 0.9748 - accuracy: 0.5971s -
Epoch 8/8
9645/9645 [==============================] - 50s 5ms/sample - loss: 0.9537 - accuracy: 0.6072


In [41]:
x_test = data[-len(X_test):]
predictions = np.argmax(model1.predict(x_test), axis=1)
with open("Glove_BidirecLSTM_y_test_sst.txt", "w") as f:
    for label in predictions:
        f.write(label.astype('str')+'\n')